In [23]:
import pandas as pd

#daraz = pd.read_csv("DarazReviewsCleaned.csv")
yelp = pd.read_csv("HFYelpCleanedplus3k.csv")
yelp

review_id             business_id                 user_id  \
0     9W0w97wiLa4KwXZ4RCE1FQ  KhXE6BV9JH6-sl6csz7E0g  RI9MqHrVqzZ0AgSXlGvx5A   
1     Yk6oEXgRwqw7Q9mZzPbS8A  luUGLqA3Gxv5raCJOAzblw  rKGTBWaFgu8a60DFqeK3Fg   
2     OC77WaRpdwiujj70cGhwIg  U7JypsxzjH5f41NFZ82bdw  eWu1xPt52B-yMZmIyBIUsw   
3     9ZufNcTWsEVFmg6WPUebyA  -t1hxZ6X-XaIU4BBUQCXGA  Fa00Bcgu0hihpDGbdHaUeA   
4     7In43zh1oVmU3Bj7gD7WSA  41QlNQkkCVvmzOPSFFz1FA  Dh6OTRg1ajZ6QLZgbOTcBQ   
...                      ...                     ...                     ...   
3636  U5EUeCuy9u97W-bKmiBDlQ  9r-sVEHe8BQn518XgJvzPA  nBJfL3u--q_1y5-LyvBjWA   
3637  lpVPRi2u4J9QsKe6rRSVjw  C809UuprygJyEgJw4wr2Pg  4kjVKQhMJKdlasEkn_Nkxw   
3638  nWcL5WeijNNklT1Xsu04lQ  icZ4cBKO1VvzWnQxgzejog  almRxI4qRYyq_ex1Byy_rw   
3639  SWRavv72TJgCDHCUwQgOEQ  Q4q9xFDxErreYTMrRshP_Q  RAjPmSA0kCytqAa_uJyyQQ   
3640  -HDaoD_dBxxzMTJnEA7Q1g  gYh91mSTbMmV3Hk9tNO7KQ  qFh5dfeWmGG-dLt3UT_kZw   

                     date  stars  \
0     2016-04-29 17:59:27    1.0   
1     2018-06-10 13:05:28    3.0   
2     2012-03-05 18:45:16    4.0   
3     2017-04-05 23:24:55    4.0   
4     2016-04-10 00:22:04    5.0   
...                   ...    ...   
3636  2017-05-01 05:59:41    1.0   
3637  2008-09-07 15:46:10    2.0   
3638  2021-02-23 23:05:45    3.0   
3639  2019-07-07 16:48:47    5.0   
3640  2014-10-11 20:39:12    1.0   

                                                   text  
0     My husband and I went there three weeks ago in...  
1     We came here on Saturday night after watching ...  
2     So I am one of those people that reviews fast ...  
3     There are several Pizza Huts in the greater Ph...  
4     I love this place! I come here all the time in...  
...                                                 ...  
3636  Went for a late night snack... I ordered two i...  
3637  Was Domino's pizza always this bad? It couldn'...  
3638  This place is in a shopping area, close to a W...  
3639  TLDR: Great option for catering events! \nI or...  
3640  I simply wanted to return some item and the st...  

[3641 rows x 6 columns]

In [3]:
!pip install -q transformers einops accelerate bitsandbytes
!pip install huggingface_hub sentencepiece
!pip install -U langchain langchain-community langchain-huggingface

In [26]:
sentences =yelp['text'][0]

sentences

from tqdm import tqdm

for i in tqdm(range(10)):
    sentences = yelp["text"][i]
    pred = []
    pred.append({
        'index':i,
        'text':sentences,
    })
print(pred) 

100%|██████████| 10/10 [00:00<?, ?it/s]

[{'index': 9, 'text': 'First Watch is an amazing place! \nIt is busy, and it sounds like your on the market place. Love it! The menu is simple, but the food is not. It is packed so you might have to wait a bit. I had to wait, but they sent me a text message when the table is ready. I ordered the bacon, which actually tasted like a million dollar. The smoked salmon is of the hook-pun intended. \n\nService is quick and friendly,and the kitchen is also doing a great job bringing out the many dishes people order to dine in, take out, or delivery. For sure one of the places in STL I will return too.'}]


In [25]:
# Load model directly
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline
model_id="gauneg/roberta-base-absa-ate-sentiment"
tokenizer = AutoTokenizer.from_pretrained(model_id)
model = AutoModelForTokenClassification.from_pretrained(model_id)
# Use a pipeline as a high-level helper

In [18]:
# after loading base model and the adapter as shown in the previous snippet
senti_pipeline = pipeline(task='ner',
                  aggregation_strategy='simple',
                  model=model,
                  tokenizer=tokenizer)

Device set to use cpu


In [19]:
single=yelp["text"][0]
single

"My husband and I went there three weeks ago in the afternoon, it was about 3 o'clock on a weekday. There were two ladies waiting ahead of us I thought they were waiting for other people, we waited about five minutes there before they were seated and there were plenty of seats. The hostess came back and then walked back again into the kitchen area for the second time without a word to us, we waited another seven minutes, I said I was going to count this, and no one ever came to seat us. A gentleman came to the greeting podium ignored us, so we left. I called to ask to speak to the manager and was told they were busy, so I reported what happened to us to the person that answered the phone and they said, OK. No apology. Nothing. We've been going to this Red Lobster since the 70's. My husband worked there when they were on the west side of Moller Rd when we were in high school. I'll never go back. It's sad whet is happening to the west side of Indy. This is what happens when you hire mann

In [20]:
single_sentence=senti_pipeline(single)
single_sentence

[{'entity_group': 'neu',
  'score': 0.37143388,
  'word': ' seats',
  'start': 271,
  'end': 276},
 {'entity_group': 'neg',
  'score': 0.68302864,
  'word': ' host',
  'start': 282,
  'end': 286},
 {'entity_group': 'neg',
  'score': 0.32282522,
  'word': 'ess',
  'start': 286,
  'end': 289},
 {'entity_group': 'neu',
  'score': 0.45550203,
  'word': ' kitchen area',
  'start': 336,
  'end': 348},
 {'entity_group': 'neg',
  'score': 0.5198935,
  'word': ' gentleman',
  'start': 493,
  'end': 502},
 {'entity_group': 'neu',
  'score': 0.32741767,
  'word': ' greeting podium',
  'start': 515,
  'end': 530},
 {'entity_group': 'neg',
  'score': 0.6297682,
  'word': ' manager',
  'start': 587,
  'end': 594},
 {'entity_group': 'neg',
  'score': 0.44676247,
  'word': ' manner',
  'start': 995,
  'end': 1001},
 {'entity_group': 'neg',
  'score': 0.68142015,
  'word': ' quality',
  'start': 1011,
  'end': 1018},
 {'entity_group': 'neg',
  'score': 0.5651219,
  'word': ' people',
  'start': 1019,
 

In [27]:
from tqdm import tqdm

for i in tqdm(range(10)):
    sentences = yelp["text"][i]
    predictions = senti_pipeline(sentences)
    print(predictions) 
    

 10%|█         | 1/10 [00:04<00:39,  4.34s/it]

[{'entity_group': 'neu', 'score': 0.37143388, 'word': ' seats', 'start': 271, 'end': 276}, {'entity_group': 'neg', 'score': 0.68302864, 'word': ' host', 'start': 282, 'end': 286}, {'entity_group': 'neg', 'score': 0.32282522, 'word': 'ess', 'start': 286, 'end': 289}, {'entity_group': 'neu', 'score': 0.45550203, 'word': ' kitchen area', 'start': 336, 'end': 348}, {'entity_group': 'neg', 'score': 0.5198935, 'word': ' gentleman', 'start': 493, 'end': 502}, {'entity_group': 'neu', 'score': 0.32741767, 'word': ' greeting podium', 'start': 515, 'end': 530}, {'entity_group': 'neg', 'score': 0.6297682, 'word': ' manager', 'start': 587, 'end': 594}, {'entity_group': 'neg', 'score': 0.44676247, 'word': ' manner', 'start': 995, 'end': 1001}, {'entity_group': 'neg', 'score': 0.68142015, 'word': ' quality', 'start': 1011, 'end': 1018}, {'entity_group': 'neg', 'score': 0.5651219, 'word': ' people', 'start': 1019, 'end': 1025}]


 20%|██        | 2/10 [00:05<00:18,  2.29s/it]

[{'entity_group': 'neg', 'score': 0.6690942, 'word': ' wait', 'start': 132, 'end': 136}, {'entity_group': 'neu', 'score': 0.5756882, 'word': ' patio', 'start': 173, 'end': 178}, {'entity_group': 'neu', 'score': 0.5373153, 'word': ' bar area', 'start': 198, 'end': 206}, {'entity_group': 'neu', 'score': 0.6205304, 'word': ' bar menu', 'start': 242, 'end': 250}, {'entity_group': 'neu', 'score': 0.69606614, 'word': ' dinner menus', 'start': 267, 'end': 279}, {'entity_group': 'neu', 'score': 0.48290637, 'word': ' meal', 'start': 312, 'end': 316}, {'entity_group': 'neg', 'score': 0.8965235, 'word': ' waiter', 'start': 323, 'end': 329}, {'entity_group': 'neu', 'score': 0.49752864, 'word': ' bar tables', 'start': 354, 'end': 364}, {'entity_group': 'neu', 'score': 0.70670426, 'word': ' food', 'start': 404, 'end': 408}, {'entity_group': 'neu', 'score': 0.51948833, 'word': ' chees', 'start': 488, 'end': 493}, {'entity_group': 'neu', 'score': 0.3229011, 'word': 'urg', 'start': 495, 'end': 498}, {'

 30%|███       | 3/10 [00:06<00:13,  1.94s/it]

...

[{'entity_group': 'neu', 'score': 0.49464032, 'word': ' pizza', 'start': 51, 'end': 56}, {'entity_group': 'neg', 'score': 0.71405566, 'word': ' owner', 'start': 221, 'end': 226}]


 90%|█████████ | 9/10 [00:12<00:01,  1.04s/it]

[{'entity_group': 'pos', 'score': 0.52820504, 'word': ' subs', 'start': 353, 'end': 357}, {'entity_group': 'pos', 'score': 0.44915965, 'word': ' quality', 'start': 366, 'end': 373}, {'entity_group': 'neu', 'score': 0.65490717, 'word': ' beer', 'start': 462, 'end': 466}]


100%|██████████| 10/10 [00:13<00:00,  1.33s/it]

[{'entity_group': 'pos', 'score': 0.52582055, 'word': ' place', 'start': 26, 'end': 31}, {'entity_group': 'pos', 'score': 0.536166, 'word': ' menu', 'start': 104, 'end': 108}, {'entity_group': 'neg', 'score': 0.46600345, 'word': ' food', 'start': 128, 'end': 132}, {'entity_group': 'neu', 'score': 0.64666283, 'word': ' table', 'start': 243, 'end': 248}, {'entity_group': 'neu', 'score': 0.4628723, 'word': ' bacon', 'start': 273, 'end': 278}, {'entity_group': 'pos', 'score': 0.48110414, 'word': ' smoked salmon', 'start': 329, 'end': 342}, {'entity_group': 'pos', 'score': 0.71559405, 'word': 'Service', 'start': 374, 'end': 381}, {'entity_group': 'pos', 'score': 0.69286, 'word': ' kitchen', 'start': 412, 'end': 419}, {'entity_group': 'pos', 'score': 0.38755563, 'word': ' dishes', 'start': 468, 'end': 474}]


In [28]:
import re

def extract_full_word(text, start, end):
    # Move left to find the start of the word
    word_start = start
    while word_start > 0 and re.match(r'\w', text[word_start - 1]):
        word_start -= 1
    # Move right to find the end of the word
    word_end = end
    while word_end < len(text) and re.match(r'\w', text[word_end]):
        word_end += 1
    return text[word_start:word_end].strip()

In [29]:
import pandas as pd
from tqdm import tqdm

# Assume yelp DataFrame is already defined and contains the required columns

def extract_aspects(n=10, threshold=0.4):
    
    arr = []

    # Loop over the first n rows by integer position
    for i in tqdm(range(n), desc="Processing reviews"):
        # .iloc is used to access rows/columns by integer position (faster and unambiguous)
        text = yelp["text"].iloc[i]
        review_id = yelp["review_id"].iloc[i]
        business_id = yelp["business_id"].iloc[i]
        user_id = yelp["user_id"].iloc[i]
        date = yelp["date"].iloc[i]
        stars = yelp["stars"].iloc[i]

        # Run your aspect-term-extraction & sentiment pipeline on the full review text
        # This typically returns a flat list of dicts, not nested lists
        # Each dict has keys: 'word', 'entity_group', 'score'
        predictions = senti_pipeline(text)

        aspect_word = [
            {"word": d["word"].strip(), "start": d["start"], "end": d["end"]}
            for d in predictions
        ]
        # Extract sentiment group label for each aspect term
        sentiments = [d["entity_group"] for d in predictions]
        # Extract and round scores to 4 decimal places as strings
        scores = [f"{d['score']:.4f}" for d in predictions]
        # Append a dictionary of all collected info into arr
        # This builds one output record per review with metadata and lists of results
        refined_aspects = []
        for aspect in aspect_word:
            full_word = extract_full_word(text, aspect["start"], aspect["end"])
            if len(full_word) >= 3:  # Filter out words shorter than 3 characters
                refined_aspects.append(full_word)
        refined_aspects = list(dict.fromkeys(refined_aspects))  # Remove duplicates while preserving order

        arr.append({
            "index":       i,
            "text":        text,
            "review_id":   review_id,
            "business_id": business_id,
            "user_id":     user_id,
            "date":        date,
            "stars":       stars,
            "aspect_words":refined_aspects,
            "sentiment":   sentiments,
            "score":       scores,
        })

    return arr

# Example usage: process first 10 reviews 
vd = extract_aspects(n=10)
print(vd)

Processing reviews:   0%|          | 0/10 [00:00<?, ?it/s]

Processing reviews: 100%|██████████| 10/10 [00:05<00:00,  1.76it/s]

[{'index': 0, 'text': "My husband and I went there three weeks ago in the afternoon, it was about 3 o'clock on a weekday. There were two ladies waiting ahead of us I thought they were waiting for other people, we waited about five minutes there before they were seated and there were plenty of seats. The hostess came back and then walked back again into the kitchen area for the second time without a word to us, we waited another seven minutes, I said I was going to count this, and no one ever came to seat us. A gentleman came to the greeting podium ignored us, so we left. I called to ask to speak to the manager and was told they were busy, so I reported what happened to us to the person that answered the phone and they said, OK. No apology. Nothing. We've been going to this Red Lobster since the 70's. My husband worked there when they were on the west side of Moller Rd when we were in high school. I'll never go back. It's sad whet is happening to the west side of Indy. This is what happ

In [30]:
from tqdm import tqdm


def extract_aspect_batches():
    arr = []
    for i in tqdm(range(len(yelp))):
        text = yelp["text"].iloc[i] # why .iloc used?
        review_id = yelp["review_id"].iloc[i]
        business_id = yelp["business_id"].iloc[i]
        user_id = yelp["user_id"].iloc[i]
        date = yelp["date"].iloc[i]
        stars = yelp["stars"].iloc[i]
        				
        predictions = senti_pipeline(text)

        # Filter out predictions with score below threshold
        # Since predictions is a flat list of dicts, iterate directly


        aspect_word = [
            {"word": d["word"].strip(), "start": d["start"], "end": d["end"]}
            for d in predictions
        ]
        # Extract sentiment group label for each aspect term
        sentiments = [d["entity_group"] for d in predictions]
        # Extract and round scores to 4 decimal places as strings
        scores = [f"{d['score']:.4f}" for d in predictions]

        refined_aspects = []
        for aspect in aspect_word:
            full_word = extract_full_word(text, aspect["start"], aspect["end"])
            if len(full_word) >= 3:  # Filter out words shorter than 3 characters
                refined_aspects.append(full_word)
        refined_aspects = list(dict.fromkeys(refined_aspects))  # Remove duplicates while preserving order

        # append a dict (or tuple) into arr
        arr.append({
            "index":       i,
            "text":        text,
            "review_id":review_id,
            "business_id":	business_id,
            "user_id":	user_id,	
            "date":date,
            "stars":stars,
            "aspect_words": refined_aspects,
            "sentiment":   sentiments,
            "score":       scores,
        })
    return arr

# run it:
results = extract_aspect_batches()
print(results)

100%|██████████| 3641/3641 [32:43<00:00,  1.85it/s] 


[{'index': 0, 'text': "My husband and I went there three weeks ago in the afternoon, it was about 3 o'clock on a weekday. There were two ladies waiting ahead of us I thought they were waiting for other people, we waited about five minutes there before they were seated and there were plenty of seats. The hostess came back and then walked back again into the kitchen area for the second time without a word to us, we waited another seven minutes, I said I was going to count this, and no one ever came to seat us. A gentleman came to the greeting podium ignored us, so we left. I called to ask to speak to the manager and was told they were busy, so I reported what happened to us to the person that answered the phone and they said, OK. No apology. Nothing. We've been going to this Red Lobster since the 70's. My husband worked there when they were on the west side of Moller Rd when we were in high school. I'll never go back. It's sad whet is happening to the west side of Indy. This is what happ

In [31]:
Yelpdf3k = pd.DataFrame(results)

# join list columns into comma-strings
Yelpdf3k["aspect_words"] = Yelpdf3k["aspect_words"].apply(lambda lst: ", ".join(lst))
Yelpdf3k["sentiment"]   = Yelpdf3k["sentiment"].apply(lambda lst: ", ".join(lst))
Yelpdf3k["score"]       = Yelpdf3k["score"].apply(lambda lst: ", ".join(lst))

# select / rename columns to taste
Yelpdf3k = Yelpdf3k[["review_id",	"business_id",	"user_id",	"date",	"stars","text", "aspect_words", "sentiment", "score"]]
Yelpdf3k.columns = ["review_id",	"business_id",	"user_id",	"date",	"stars","text", "aspect words", "sentiment", "sentiment score"]


In [32]:
Yelpdf3k.to_csv("yelp3k_Aspects_result.csv", index=False, encoding="utf-8")
Yelpdf3k

review_id             business_id                 user_id  \
0     9W0w97wiLa4KwXZ4RCE1FQ  KhXE6BV9JH6-sl6csz7E0g  RI9MqHrVqzZ0AgSXlGvx5A   
1     Yk6oEXgRwqw7Q9mZzPbS8A  luUGLqA3Gxv5raCJOAzblw  rKGTBWaFgu8a60DFqeK3Fg   
2     OC77WaRpdwiujj70cGhwIg  U7JypsxzjH5f41NFZ82bdw  eWu1xPt52B-yMZmIyBIUsw   
3     9ZufNcTWsEVFmg6WPUebyA  -t1hxZ6X-XaIU4BBUQCXGA  Fa00Bcgu0hihpDGbdHaUeA   
4     7In43zh1oVmU3Bj7gD7WSA  41QlNQkkCVvmzOPSFFz1FA  Dh6OTRg1ajZ6QLZgbOTcBQ   
...                      ...                     ...                     ...   
3636  U5EUeCuy9u97W-bKmiBDlQ  9r-sVEHe8BQn518XgJvzPA  nBJfL3u--q_1y5-LyvBjWA   
3637  lpVPRi2u4J9QsKe6rRSVjw  C809UuprygJyEgJw4wr2Pg  4kjVKQhMJKdlasEkn_Nkxw   
3638  nWcL5WeijNNklT1Xsu04lQ  icZ4cBKO1VvzWnQxgzejog  almRxI4qRYyq_ex1Byy_rw   
3639  SWRavv72TJgCDHCUwQgOEQ  Q4q9xFDxErreYTMrRshP_Q  RAjPmSA0kCytqAa_uJyyQQ   
3640  -HDaoD_dBxxzMTJnEA7Q1g  gYh91mSTbMmV3Hk9tNO7KQ  qFh5dfeWmGG-dLt3UT_kZw   

                     date  stars  \
0     2016-04-29 17:59:27    1.0   
1     2018-06-10 13:05:28    3.0   
2     2012-03-05 18:45:16    4.0   
3     2017-04-05 23:24:55    4.0   
4     2016-04-10 00:22:04    5.0   
...                   ...    ...   
3636  2017-05-01 05:59:41    1.0   
3637  2008-09-07 15:46:10    2.0   
3638  2021-02-23 23:05:45    3.0   
3639  2019-07-07 16:48:47    5.0   
3640  2014-10-11 20:39:12    1.0   

                                                   text  \
0     My husband and I went there three weeks ago in...   
1     We came here on Saturday night after watching ...   
2     So I am one of those people that reviews fast ...   
3     There are several Pizza Huts in the greater Ph...   
4     I love this place! I come here all the time in...   
...                                                 ...   
3636  Went for a late night snack... I ordered two i...   
3637  Was Domino's pizza always this bad? It couldn'...   
3638  This place is in a shopping area, close to a W...   
3639  TLDR: Great option for catering events! \nI or...   
3640  I simply wanted to return some item and the st...   

                                           aspect words  \
0     seats, hostess, kitchen area, gentleman, greet...   
1     wait, patio, bar area, bar menu, dinner menus,...   
2     food, management, interior, people, burger, pa...   
3                  customer, service, delivery, quality   
4     place, plants, garden, hydrangea plant, select...   
...                                                 ...   
3636  snack, ice cream concrete, mixers, employees, ...   
3637         pizza, pizzas, options, breadsticks, wings   
3638           coffee, chocolate, hot chocolate, prices   
3639  catering, taco bar, employee, serving ware, si...   
3640                                              staff   

                                              sentiment  \
0      neu, neg, neg, neu, neg, neu, neg, neg, neg, neg   
1     neg, neu, neu, neu, neu, neu, neg, neu, neu, n...   
2     pos, neu, pos, neg, pos, pos, neu, neu, neu, n...   
3                          pos, pos, pos, neg, neg, neu   
4                     pos, neu, neu, neu, neu, pos, pos   
...                                                 ...   
3636  neu, neu, neg, neg, neg, neu, neu, neg, neg, n...   
3637                            neg, neg, pos, pos, neu   
3638                                 neu, neu, pos, neg   
3639  pos, neu, neu, pos, neu, neu, neu, neu, neu, n...   
3640                                      neg, neg, neg   

                                        sentiment score  
0     0.3714, 0.6830, 0.3228, 0.4555, 0.5199, 0.3274...  
1     0.6691, 0.5757, 0.5373, 0.6205, 0.6961, 0.4829...  
2     0.6074, 0.4728, 0.4246, 0.4223, 0.7111, 0.4608...  
3        0.5132, 0.4385, 0.5535, 0.7615, 0.4534, 0.4005  
4     0.5419, 0.4585, 0.4626, 0.4575, 0.3292, 0.4587...  
...                                                 ...  
3636  0.7065, 0.3535, 0.2964, 0.5566, 0.7972, 0.6820...  
3637             0.6048, 0.5881, 0